In [110]:
import pandas as pd
import re
from datetime import datetime
import numpy as np

In [111]:
year = '2019'
data = pd.read_csv('data/raw-data/wnba-raw-pbp-'+year+'.csv',)

In [112]:
data.columns

Index(['evt', 'cl', 'de', 'locX', 'locY', 'opt1', 'opt2', 'mtype', 'etype',
       'opid', 'tid', 'pid', 'hs', 'vs', 'epid', 'oftid', 'gid', 'year',
       'gameType', 'quarter', 'date', 'homeTeam', 'awayTeam'],
      dtype='object')

In [113]:
df = data[['date','gid','gameType','homeTeam','awayTeam','quarter','cl','hs','vs','de']]
df.columns = ['Date','GameID','GameType','HomeTeam','AwayTeam','Quarter','Time','HomeScore','AwayScore','EventDescription']
if year not in ['2016','2017']:
    extracols = data[['locX','locY','opt1','opt2','mtype','etype','opid','tid','pid','epid','oftid','ord']]
else:
    extracols = data[['locX','locY','opt1','opt2','mtype','etype','opid','tid','pid','epid','oftid']]

In [114]:
#add all of the columns so they are in the same order for all years
list_of_columns = ['WinningTeam', 'Event', 'EventTeam', 'EventPlayer', 'Shooter',
       'SpecificShotType', 'ShotType', 'ShotOutcome', 'ShooterNumPTS',
       'Foul', 'FoulType', 'FoulNumFouls', 'FoulNumShots', 'TechnicalType',
       'Rebounder', 'ReboundType', 'RebounderNumOffRebounds', 'RebounderNumDefRebounds',
       'Assist', 'AssistNumAST', 'Block','BlockNumBLK', 
       'Turnover', 'TurnoverType', 'TurnoverNumTO', 'Steal', 'StealNumSTL',
       'SubstitutionOut', 'SubstitutionIn',
       'JumpBallPlayer1', 'JumpBallPlayer2', 'JumpBallPlayerPoss', 'JumpBallTeamPoss', 
       'Timeout', 'TimeoutType', 'StoppageType', 'InstantReplayType',
        'Violation','ViolationType']

for new_column in list_of_columns:
    df[new_column] = ""
    
df = df.join(extracols)

<ipython-input-114-77d28ef43c99>:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[new_column] = ""


In [115]:
df

Date      GameID        GameType HomeTeam AwayTeam  Quarter  \
0      2016-05-14  1021600001  regular season      IND      DAL        1   
1      2016-05-14  1021600001  regular season      IND      DAL        1   
2      2016-05-14  1021600001  regular season      IND      DAL        1   
3      2016-05-14  1021600001  regular season      IND      DAL        1   
4      2016-05-14  1021600001  regular season      IND      DAL        1   
...           ...         ...             ...      ...      ...      ...   
86294  2016-10-20  1041600405        playoffs      MIN      LAS        4   
86295  2016-10-20  1041600405        playoffs      MIN      LAS        4   
86296  2016-10-20  1041600405        playoffs      MIN      LAS        4   
86297  2016-10-20  1041600405        playoffs      MIN      LAS        4   
86298  2016-10-20  1041600405        playoffs      MIN      LAS        4   

          Time  HomeScore  AwayScore  \
0        10:00          0          0   
1        10:00          0          0   
2        09:46          0          0   
3        09:38          0          0   
4        09:26          0          0   
...        ...        ...        ...   
86294  00:03.1         76         75   
86295  00:02.1         76         77   
86296  00:00.0         76         77   
86297  00:00.0         76         77   
86298  00:00.0         76         77   

                                        EventDescription  ... locY opt1 opt2  \
0                                           Start Period  ...  -80    0    0   
1      Jump Ball Larkins vs Paris (Christmas gains po...  ...  -80    0    0   
2      [DAL] Paris Turnover : Lost Ball (1 TO) Steal:...  ...  -80    1    0   
3      [IND] Wheeler Turnover : Out of Bounds - Bad P...  ...  -80    0    0   
4                       [DAL] Christmas 3pt Shot: Missed  ...   -6    3    0   
...                                                  ...  ...  ...  ...  ...   
86294               [LAS] Ogwumike Rebound (Off:6 Def:6)  ...  -80    1    0   
86295     [LAS 77-76] Ogwumike Layup Shot: Made (12 PTS)  ...    3    2    0   
86296                      [MIN] Whalen 3pt Shot: Missed  ...  397    3    0   
86297                                 [LAS] Team Rebound  ...  -80    0    0   
86298                                         End Period  ...  -80    0    0   

      mtype etype      opid         tid     pid      epid       oftid  
0         0    12       NaN           0       0       NaN           0  
1         0    10  201907.0  1611661325  201503  202640.0  1611661321  
2         2     5  201503.0  1611661321  201907       NaN  1611661321  
3        45     5       NaN  1611661325  204365       NaN  1611661325  
4         1     2       NaN  1611661321  202640       NaN  1611661321  
...     ...   ...       ...         ...     ...       ...         ...  
86294     0     4       NaN  1611661320  203014       NaN  1611661320  
86295     5     1       NaN  1611661320  203014       NaN  1611661320  
86296     1     2       NaN  1611661324  100915       NaN  1611661324  
86297     0     4       NaN  1611661320       0       NaN  1611661324  
86298     0    13       NaN           0       0       NaN  1611661320  

[86299 rows x 60 columns]

In [116]:
#get the winners of each game
g = df.groupby(['GameID'])
d = g.last()
d = d.reset_index()
game_winners = {}
for row in range(len(d)):
    if int(d.loc[row,'HomeScore']) > int(d.loc[row,'AwayScore']):
        game_winners[d.loc[row,'GameID']] = d.loc[row,'HomeTeam']
    else:
        game_winners[d.loc[row,'GameID']] = d.loc[row,'AwayTeam'] 

In [117]:
#team ids to use for jump ball possession
team_ids = {0: np.nan,
 82: 'CHN',
 1611661313: 'NYL',
 1611661317: 'PHO',
 1611661319: 'LVA',
 1611661320: 'LAS',
 1611661321: 'DAL',
 1611661322: 'WAS',
 1611661323: 'CON',
 1611661324: 'MIN',
 1611661325: 'IND',
 1611661328: 'SEA',
 1611661329: 'CHI',
 1611661330: 'ATL'}

In [118]:
event_list = ['Rebound','Timeout','Substitution replaced by',
              '(?<!Turnover : )Foul','Turnover','Violation','Unsportsmanlike Technical',
              '(?<!Free Throw )Technical','Ejection','3pt Shot','[Ss]hot',
             'Free Throw Technical(?! [1-3])','Free Throw [1-3] of [1-3]',
               'Free Throw Flagrant [1-3] of [1-3]',
               'Free Throw Clear Path [1-3] of [1-3]',
               'Free Throw Technical [1-3] of [1-3]']
free_throws = ['Free Throw Technical','Free Throw 1 of 2','Free Throw 2 of 2',
               'Free Throw 1 of 1','Free Throw 1 of 3','Free Throw 2 of 3','Free Throw 3 of 3',
               'Free Throw Flagrant 1 of 2','Free Throw Flagrant 2 of 2', 'Free Throw Flagrant 1 of 1',
               'Free Throw Clear Path 1 of 2','Free Throw Clear Path 2 of 2',
               'Free Throw Technical 1 of 2','Free Throw Technical 2 of 2','Free Throw Technical 1 of 1']

event2_list = ['Assist','Block','Steal']

game_events = ['Period End','Period Start','Start Period','End Period',
               'Instant Replay','InstantReplay',
               'Jump Ball','Stoppage','Timeout',
               'Delay Technical','Double Technical','Too Many Players Technical',
               'Foul : Double Personal']
techs = ['Delay Technical','Double Technical','Too Many Players Technical']
event_list = '|'.join(event_list)
event2_list = '|'.join(event2_list)
game_events = '|'.join(game_events)


def function_test(string):
    #match = re.match(r"\[(?P<team_name>[A-Z]{3}).*\] (?P<player>\w+) (?P<specific_event>[\w\s]*)[12\:]? (?P<remaining_string>.*)", string)
    #match = re.match(r"\[(?P<team_name>[A-Z]{3}).*\] (?P<player>[\w\s\-]*) (?P<specific_event>"+test+") [12\:\(]? (?P<remaining_string>.*)", string)
    #match = re.match(r"\[(?P<team_name>[A-Z]{3}).*\] (?P<player>[\w\s\-]*) (?P<event>"+test+")([:\s]*)?(?P<specific_event>[\w\s\-]*)?(?P<outcome>"+outcomes+")?(?P<stat1>\(.{1,12}\))?(?P<event2>"+test2+")?([:\s]*)?(?P<player2>[\w\s\-]*)?(?P<stat2>\(.*\))?", string)
    string = re.sub("G(\w){1,2}lich","Gulich",string)
    print(string)
    match = re.match(r"\[(?P<team_name>[A-Z]{3}).*\]([:\s]*)?(?P<player>[\w\s\-]*)([:\s]*)?(?P<event>"+event_list+")([:\s]*)?(?P<specific_event>[\w\s\-]*)?(?P<stat1>\(.{1,12}\))?([:\s]*)?(?P<event2>"+event2_list+")?([:\s]*)?(?P<player2>[\w\s\-]*)?(?P<stat2>\(.*\))?", string)
    if match:
        #print(match.group('team_name'))
        #print(match.group('player'))
        print(match.group('event'))
        #print(match.group('specific_event'))
        #print(match.group('stat1'))
        #print(match.group('event2'))
        #print(match.group('player2'))
        #print(match.group('stat2'))
        
    else:
        pass
            
            
[function_test(str(x)) for x in df['EventDescription']]


Start Period
Jump Ball Larkins vs Paris (Christmas gains possession)
[DAL] Paris Turnover : Lost Ball (1 TO) Steal:Larkins (1 ST)
Turnover
[IND] Wheeler Turnover : Out of Bounds - Bad Pass Turnover (1 TO)
Turnover
[DAL] Christmas 3pt Shot: Missed
Shot
[IND] Larkins Rebound (Off:0 Def:1)
Rebound
[DAL] Paris Foul: Shooting (1 PF) (2 FTA)
Foul
[IND 1-0] Catchings Free Throw 1 of 2 (1 PTS)
Free Throw 1 of 2
[IND 2-0] Catchings Free Throw 2 of 2 (2 PTS)
Free Throw 2 of 2
[DAL 3-2] Phillips 3pt Shot: Made (3 PTS) Assist: Sims (1 AST)
Shot
[IND 4-3] Wheeler Pullup Jump shot: Made (2 PTS) Assist: Larkins (1 AST)
shot
[DAL] Paris Jump Shot: Missed Block: Catchings (1 BLK)
Shot
[DAL] Paris Rebound (Off:1 Def:0)
Rebound
Jump Ball Catchings vs Paris (Phillips gains possession)
[DAL 5-4] Pierson Step Back Jump shot: Made (2 PTS)
shot
[IND] Mitchell Jump Shot: Missed
Shot
[IND] Larkins Rebound (Off:1 Def:1)
Rebound
[DAL] Paris Foul: Shooting (2 PF) (2 FTA)
Foul
[IND 5-5] Larkins Free Throw 1 of 2 (1

Free Throw 1 of 2
[CHI 91-68] Boyette Free Throw 2 of 2 (4 PTS)
Free Throw 2 of 2
[CON 70-91] Bentley Jump Shot: Made (14 PTS)
Shot
[CHI 93-70] Laney Cutting Layup Shot: Made (8 PTS) Assist: Faulkner (6 AST)
Shot
[CON] Bentley Jump Shot: Missed
Shot
[CHI] Faulkner Rebound (Off:0 Def:2)
Rebound
End Period
Start Period
Jump Ball Appel-Marinelli vs Williams (Cortijo gains possession)
[ATL 2-0] McCoughtry Jump Shot: Made (2 PTS) Assist: Lyttle (1 AST)
Shot
[SAN] Currie Layup Shot: Missed Block: Lyttle (1 BLK)
Shot
[SAN] Team Rebound
Rebound
[SAN 2-2] McBride Jump Shot: Made (2 PTS) Assist: Currie (1 AST)
Shot
[ATL 4-2] Hayes Driving Layup Shot: Made (2 PTS) Assist: Cortijo (1 AST)
Shot
[SAN] Appel-Marinelli Turnover : Bad Pass (1 TO) Steal:McCoughtry (1 ST)
Turnover
[SAN] Appel-Marinelli Foul: Shooting (1 PF) (2 FTA)
Foul
[ATL 5-2] Williams Free Throw 1 of 2 (1 PTS)
Free Throw 1 of 2
[ATL] Williams Free Throw 2 of 2 Missed
Free Throw 2 of 2
[SAN] Appel-Marinelli Rebound (Off:0 Def:1)
Rebou

[DAL] Sims 3pt Shot: Missed
Shot
[WAS] Meesseman Rebound (Off:1 Def:3)
Rebound
[WAS] Vaughn Turnover : Traveling (2 TO)
Turnover
[WAS] Cloud Foul: Shooting (2 PF) (2 FTA)
Foul
[WAS] Thibault Technical
Technical
[WAS] Team Timeout : Regular
Timeout
[WAS] Cloud Substitution replaced by Hartley
Substitution replaced by
[DAL 7-4] Sims Free Throw Technical (1 PTS)
Free Throw Technical
[DAL 8-4] Sims Free Throw 1 of 2 (2 PTS)
Free Throw 1 of 2
[DAL 9-4] Sims Free Throw 2 of 2 (3 PTS)
Free Throw 2 of 2
[WAS] Dolson Jump Shot: Missed
Shot
[DAL] Pierson Rebound (Off:0 Def:1)
Rebound
[DAL] Pierson Foul: Offensive Charge (2 PF)
Foul
[DAL] Pierson Turnover : Foul (2 TO)
Turnover
[DAL] Sims Substitution replaced by Kiesel
Substitution replaced by
[WAS] Vaughn Substitution replaced by Copper
Substitution replaced by
[DAL] Pierson Foul: Personal (3 PF)
Foul
[DAL] Phillips Substitution replaced by Hooper
Substitution replaced by
[DAL] Pierson Substitution replaced by Plaisance
Substitution replaced by

Turnover
[WAS 66-94] Vaughn Layup Shot: Made (6 PTS) Assist: Dimitrakou (1 AST)
Shot
[LAS] Wauters Foul: Shooting (1 PF) (1 FTA)
Foul
[WAS 67-94] Vaughn Free Throw 1 of 1 (7 PTS)
Free Throw 1 of 1
[LAS 97-67] Knight 3pt Shot: Made (3 PTS) Assist: Dubljevic (1 AST)
Shot
[WAS] Vaughn Jump Shot: Missed
Shot
[LAS] Wauters Rebound (Off:0 Def:1)
Rebound
[LAS] Dubljevic 3pt Shot: Missed
Shot
[WAS] Dimitrakou Rebound (Off:0 Def:1)
Rebound
End Period
Start Period
Jump Ball Larkins vs Williams (Hayes gains possession)
[ATL] McCoughtry Turnover : Lost Ball (1 TO) Steal:Catchings (1 ST)
Turnover
[IND] Johnson Layup Shot: Missed
Shot
[ATL] Lyttle Rebound (Off:0 Def:1)
Rebound
[ATL] McCoughtry Turnover : Bad Pass (2 TO) Steal:Johnson (1 ST)
Turnover
[IND] Coleman Running Finger Roll Layup Shot: Missed
Shot
[ATL] Clarendon Rebound (Off:0 Def:1)
Rebound
[ATL 2-0] McCoughtry Driving Layup Shot: Made (2 PTS)
Shot
[IND] Catchings Turnover : Bad Pass (1 TO)
Turnover
[ATL] Clarendon Turnover : Bad Pass (1 

[WAS 52-52] Vaughn Free Throw 2 of 2 (6 PTS)
Free Throw 2 of 2
[CON] Tuck 3pt Shot: Missed
Shot
[CON] Team Rebound
Rebound
[WAS] Ruffin-Pratt Foul: Loose Ball (5 PF)
Foul
[WAS] Ruffin-Pratt Substitution replaced by Hill
Substitution replaced by
[CON] Thomas Jump Shot: Missed
Shot
[CON] Thomas Rebound (Off:1 Def:6)
Rebound
[CON] Team Turnover : Shot Clock Turnover
Shot
[WAS] Vaughn Turnover : Out of Bounds Lost Ball Turnover (1 TO)
Turnover
[CON] Banham Substitution replaced by Bentley
Substitution replaced by
[CON 54-52] Tuck Layup Shot: Made (5 PTS)
Shot
[WAS 54-54] Hill Jump Shot: Made (16 PTS)
Shot
[CON 56-54] Thomas Jump Shot: Made (15 PTS) Assist: Tuck (1 AST)
Shot
[WAS 56-56] Copper Driving Layup Shot: Made (3 PTS)
Shot
[CON] Tuck Jump Shot: Missed
Shot
[CON] Team Rebound
Rebound
[WAS] Hawkins Substitution replaced by Meesseman
Substitution replaced by
[CON 58-56] Bone Jump Shot: Made (4 PTS) Assist: Bentley (5 AST)
Shot
[CON] Thomas Foul: Personal Block (2 PF)
Foul
[WAS] Vaughn 

...

Shot
[ATL] Williams Rebound (Off:3 Def:2)
Rebound
[ATL 9-5] McCoughtry 3pt Shot: Made (5 PTS) Assist: Clarendon (3 AST)
Shot
[SEA] Clark Jump Shot: Missed
Shot
[SEA] Clark Rebound (Off:1 Def:0)
Rebound
[SEA 8-9] Stewart 3pt Shot: Made (5 PTS) Assist: Clark (1 AST)
Shot
[SEA] Bird Foul: Personal (1 PF)
Foul
Timeout : Official
[SEA] Langhorne Substitution replaced by Tokashiki
Substitution replaced by
[ATL] McCoughtry Jump Shot: Missed
Shot
[SEA] Bird Rebound (Off:0 Def:2)
Rebound
[ATL] Williams Foul: Defense 3 Second (1 PF)
Foul
[SEA 9-9] Loyd Free Throw Technical (1 PTS)
Free Throw Technical
[SEA] Clark Jump Shot: Missed
Shot
[ATL] Williams Rebound (Off:3 Def:3)
Rebound
[ATL 11-9] McCoughtry Jump Shot: Made (7 PTS)
Shot
[ATL] Clarendon Foul: Personal (1 PF)
Foul
[SEA] Loyd Jump Shot: Missed
Shot
[ATL] Team Rebound
Rebound
[SEA] Tokashiki Foul: Personal (1 PF)
Foul
[ATL] Holmes 3pt Shot: Missed
Shot
[SEA] Stewart Rebound (Off:0 Def:1)
Rebound
[SEA 11-11] Stewart Driving Layup Shot: Made

[PHO 21-33] Xargay Jump Shot: Made (4 PTS)
Shot
[MIN] Moore Layup Shot: Missed
Shot
[MIN] Team Rebound
Rebound
[PHO] Dupree Foul: Loose Ball (1 PF) (2 FTA)
Foul
[MIN 34-21] Moore Free Throw 1 of 2 (13 PTS)
Free Throw 1 of 2
[MIN 35-21] Moore Free Throw 2 of 2 (14 PTS)
Free Throw 2 of 2
[PHO 23-35] Bonner Driving Layup Shot: Made (2 PTS)
Shot
[MIN] Howard Foul: Shooting (1 PF) (1 FTA)
Foul
[PHO 24-35] Bonner Free Throw 1 of 1 (3 PTS)
Free Throw 1 of 1
[MIN] Whalen Turnover : Traveling (1 TO)
Turnover
End Period
Start Period
[MIN] Moore Jump Shot: Missed
Shot
[PHO] Taylor Rebound (Off:0 Def:1)
Rebound
[PHO] Bonner Turnover : Bad Pass (2 TO) Steal:Perkins (2 ST)
Turnover
[MIN] Augustus Jump Shot: Missed
Shot
[PHO] Bonner Rebound (Off:0 Def:3)
Rebound
[PHO] Dupree Jump Shot: Missed
Shot
[PHO] Bass Rebound (Off:1 Def:0)
Rebound
[PHO] Bass Layup Shot: Missed
Shot
[MIN] Moore Rebound (Off:1 Def:2)
Rebound
[MIN] Whalen Jump Shot: Missed
Shot
[MIN] Brunson Rebound (Off:1 Def:3)
Rebound
[PHO] Bo

Rebound
[LAS] Toliver 3pt Shot: Missed
Shot
[CHI] Boyette Rebound (Off:3 Def:2)
Rebound
[LAS] Dabovic Foul: Personal (1 PF)
Foul
[CHI] Pondexter Substitution replaced by Dos Santos
Substitution replaced by
[LAS] Lavender Foul: Shooting (2 PF) (2 FTA)
Foul
[CHI 42-45] Vandersloot Free Throw 1 of 2 (3 PTS)
Free Throw 1 of 2
[CHI 43-45] Vandersloot Free Throw 2 of 2 (4 PTS)
Free Throw 2 of 2
[LAS] Toliver Substitution replaced by Parker
Substitution replaced by
[LAS] Parker Turnover : Bad Pass (3 TO) Steal:Young (1 ST)
Turnover
[CHI] Boyette Jump Shot: Missed
Shot
[LAS] Ogwumike Rebound (Off:0 Def:5)
Rebound
[LAS] Beard Turnover : Step Out of Bounds Turnover (1 TO)
Turnover
[CHI 45-45] Breland Layup Shot: Made (8 PTS) Assist: Boyette (1 AST)
Shot
[LAS] Parker 3pt Shot: Missed
Shot
[CHI] Boyette Rebound (Off:3 Def:3)
Rebound
[CHI 47-45] Vandersloot Driving Layup Shot: Made (6 PTS) Assist: Young (3 AST)
Shot
[LAS] Parker 3pt Shot: Missed
Shot
[CHI] Breland Rebound (Off:0 Def:4)
Rebound
[CHI

Rebound
[LAS 20-21] Gray Driving Layup Shot: Made (2 PTS)
Shot
[MIN] Howard Turnover : Traveling (1 TO)
Turnover
[LAS] Carson Layup Shot: Missed Block: Moore (2 BLK)
Shot
[MIN] Whalen Rebound (Off:1 Def:2)
Rebound
[LAS] Gray Foul: Shooting (1 PF) (2 FTA)
Foul
[MIN 22-20] Whalen Free Throw 1 of 2 (3 PTS)
Free Throw 1 of 2
[MIN] Montgomery Substitution replaced by Fowles
Substitution replaced by
[MIN] Whalen Free Throw 2 of 2 Missed
Free Throw 2 of 2
[LAS] Carson Rebound (Off:1 Def:2)
Rebound
[LAS] Team Turnover : Backcourt Turnover
Turnover
[MIN] Whalen Turnover : Traveling (1 TO)
Turnover
[LAS] Ogwumike 3pt Shot: Missed
Shot
[LAS] Team Rebound
Rebound
End Period
Start Period
[MIN] Howard Step Back Jump shot: Missed
shot
[LAS] Gray Rebound (Off:0 Def:1)
Rebound
[LAS] Parker Jump Shot: Missed
Shot
[MIN] Fowles Rebound (Off:1 Def:3)
Rebound
[MIN] Augustus Jump Shot: Missed
Shot
[LAS] Parker Rebound (Off:0 Def:1)
Rebound
[LAS 22-22] Lavender Jump Shot: Made (2 PTS) Assist: Parker (2 AST)
S

[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,

In [119]:
#to make tests quicker
#df = df.loc[0:5000,:]

In [120]:
#shots that are too descriptive and don't parse correctly
adj_list = ['3pt','Jump','Pull-up','Pull-Up','Layup','Dunk','Driving','Cutting','Floating','Bank','Pullup','Turnaround','Step','Back','Fadeaway','Hook','Driving','Putback','Alley','Oop','Reverse','Running','Finger','Roll','Tip','No']
def append_shot_adj(player,event):
    word_list = re.split(" ",player)
    words = [word for word in word_list if word in adj_list ]
    words.append(event)
    string = " ".join(words)
    return string
def separate_player(player):
    word_list = re.split(" ",player)
    words = [word for word in word_list if word not in adj_list ]
    string = " ".join(words)
    return(string)

#an example
player = "Bird Turnaround"
event = "Jump shot"
append_shot_adj(player,event)
separate_player(player)

'Bird'

In [121]:
#test = df[df['GameID']==1011800008]
#df = test.reset_index()

In [122]:
temp_df_dts = []
temp_df_dfs = []
for row in range(len(df['EventDescription'])):
    df.loc[row,'WinningTeam'] = game_winners[df.loc[row,'GameID']]
    string = df.loc[row,'EventDescription']
    string = re.sub("G(\w){1,2}lich","Gulich",string)
    match = re.match(r"\[(?P<team_name>[A-Z]{3}).*\]([:\s]*)?(?P<player>[\w\s\-']*)([:\s]*)?(?P<event>"+event_list+")([:\s]*)?(?P<specific_event>[\w\s\-]*)?(?P<stat1>\(.{1,12}\))?([:\s]*)?(?P<event2>"+event2_list+")?([:\s]*)?(?P<player2>[\w\s\-']*)?(?P<stat2>\(.*\))?", string)
    if match:
        team = (match.group('team_name'))
        player = (match.group('player'))
        event = (match.group('event'))
        event = append_shot_adj(player,event) #fix shots that didn't parse
        player = separate_player(player) #get shooter name (remove shot adj)
        player = re.sub(' $','',player) #remove space at the end of player name
        specific_event = (match.group('specific_event'))
        specific_event = re.sub(' $','',specific_event) #remove space
        stat1 = (match.group('stat1'))
        event2 = (match.group('event2'))
        player2 = (match.group('player2'))
        player2 = re.sub(' $','',player2) #remove space
        stat2 = (match.group('stat2'))
        
        #fix blocks
        if match.group('specific_event') == 'Missed Block':
            specific_event = 'Missed'
            event2 = 'Block'
            match3 = re.match(r".*Missed Block: (?P<player2>[\w\s\-']*)(?P<stat2>\(.*\))?",string)
            player2 = (match3.group('player2'))
            stat2 = (match3.group('stat2'))
            
        #fix shot clock turnovers
        if specific_event == "Clock Turnover":
            event = 'Turnover'
            player = 'Team'
            specific_event = "Shot Clock Turnover"
            
            
        #get the stats numbers in parenthesis
        num1 = stat1
        num2 = stat2
        if stat1 is not None:
            match4 = re.match(r"[A-Za-z:\(\)\s]*(?P<number>[0-9]+)[A-Za-z:\(\)\s]*(?P<number2>[0-9]+)?",stat1)
            num1 = (match4.group('number'))
            num2 = (match4.group('number2'))
        if stat2 is not None:
            match4 = re.match(r"[A-Za-z:\(\)\s]*(?P<number>[0-9]+)[A-Za-z:\(\)\s]*(?P<number2>[0-9]+)?",stat2)
            num2 = (match4.group('number'))
        
        df.loc[row,'Event'] = event
        df.loc[row,'EventTeam'] = team_ids[df.loc[row,'tid']]
    
    #EVENT 1
        #Substitutions
        if (match.group('event')) == 'Substitution replaced by':
            df.loc[row,'Event'] = 'Substitution'
            df.loc[row,'SubstitutionOut'] = player
            player2 = specific_event
            df.loc[row,'SubstitutionIn'] = player2
        else:
            df.loc[row,'EventPlayer'] = player
        
        #Shots
        if re.match(".*[Ss]hot.*",event) or event in free_throws:
            df.loc[row,'Shooter'] = player
            df.loc[row,'SpecificShotType'] = event
            df.loc[row,'ShotType'] = '2pt Shot'
            if event == '3pt Shot':
                df.loc[row,'ShotType'] = '3pt Shot'
            if (match.group('event')) in free_throws:
                df.loc[row,'ShotType'] = 'Free Throw'
            df.loc[row,'Event'] = df.loc[row,'ShotType']
            
            df.loc[row,'ShotOutcome'] = specific_event
            #if specific_event not in ['Made','Missed']:
            #    print(specific_event)
            if (match.group('specific_event')) == '':
                df.loc[row,'ShotOutcome'] = 'Made'
                df.loc[row,'ShooterNumPTS'] = num1
        
        #Fouls
        if event == 'Foul':
            df.loc[row,'Foul'] = player
            df.loc[row,'FoulType'] = specific_event
            df.loc[row,'FoulNumFouls'] = num1
            df.loc[row,'FoulNumShots'] = num2
        
        #Turnovers
        if event == 'Turnover':
            df.loc[row,'Turnover'] = player
            df.loc[row,'TurnoverType'] = specific_event
            df.loc[row,'TurnoverNumTO'] = num1
            
        #Violations
        if event == 'Violation':
            df.loc[row,'Violation'] = player
            df.loc[row,'ViolationType'] = specific_event
            
        #Timeout
        if event == 'Timeout':
            df.loc[row,'Timeout'] = team
            df.loc[row,'TimeoutType'] = specific_event
        
        #Rebounds
        if event == 'Rebound':
            df.loc[row,'Rebounder'] = player
            if (df.loc[row,'tid']) == (df.loc[row,'oftid']): #use compare offensive team id to player team id
                df.loc[row,'ReboundType'] = 'Offensive'
            else:
                df.loc[row,'ReboundType'] = 'Defensive'
            df.loc[row,'RebounderNumOffRebounds'] = num1 #get player rebounding stats
            df.loc[row,'RebounderNumDefRebounds'] = num2
            
    #EVENT 2
        #Assists
        if event2 == 'Assist':
            df.loc[row,'Assist'] = player2
            df.loc[row,'AssistNumAST'] = num2
            
        #Blocks
        if event2 == 'Block':
            df.loc[row,'Block'] = player2
            df.loc[row,'BlockNumBLK'] = num2
            
        #Steals
        if event2 == 'Steal':
            df.loc[row,'Steal'] = player2
            df.loc[row,'StealNumSTL'] = num2
        
        
    else: #other game events that aren't player/team specific
        match2 = re.match(r"(?P<game_event>"+game_events+")?.*",string)
        event = (match2.group('game_event'))
        df.loc[row,'Event'] = event
        df.loc[row,'EventTeam'] = team_ids[df.loc[row,'tid']]
        
        #Jump Ball
        if event == 'Jump Ball':
            match3 = re.match(r"Jump Ball (?P<jb1>[\w\s\-']*) vs (?P<jb2>[\w\s\-']*)(\s?\(?(?P<jb3>[\w\s\-']*)gains possession\))?",string)
            df.loc[row,'JumpBallPlayer1'] = (match3.group('jb1'))
            df.loc[row,'JumpBallPlayer2'] = (match3.group('jb2'))
            df.loc[row,'JumpBallPlayerPoss'] = (match3.group('jb3'))
            df.loc[row,'JumpBallTeamPoss'] = team_ids[df.loc[row,'tid']] #team id is the team that gained poss
            
        #Instant Replay
        if event == 'Instant Replay' or event == 'InstantReplay':
            df.loc[row,'Event'] = 'Instant Replay'
            match3 = re.match(r"Instant[ ]?Replay[ ]?[-]? (?P<type>[\w\s\-]*)",string)
            df.loc[row,'InstantReplayType'] = (match3.group('type'))
            
        #Stoppage
        if event == 'Stoppage':
            match3 = re.match(r"Stoppage([:\s]*)?(?P<type>[\w\s\-]*)",string)
            df.loc[row,'StoppageType'] = (match3.group('type'))
            
        #Timeout
        if event == 'Timeout':
            match3 = re.match(r"Timeout([:\s]*)?(?P<type>[\w\s\-]*)",string)
            df.loc[row,'Timeout'] = (match3.group('type'))
            df.loc[row,'TimeoutType'] = (match3.group('type'))
            
        #Technical
        if event in techs:
            df.loc[row,'Event'] = 'Technical'
            df.loc[row,'TechnicalType'] = event
            if event in ['Delay Technical','Too Many Player Technical']:
                match3 = re.match(r"[\w\s']*- (?P<team>[A-Z]{3})( \((?P<fta>[0-9]) FTA\))?",string)
                df.loc[row,'EventTeam'] = (match3.group('team'))
            if event == 'Double Technical':
                match3 = re.match(r"Double Technical - (?P<p1>[\w\s\-']*), (?P<p2>[\w\s\-']*)",string)
                df.loc[row,'EventPlayer'] = (match3.group('p1'))
                df.loc[row,'TechnicalType'] = 'Double Technical'
                dtrow = df.iloc[row]
                dtrow['EventPlayer'] = match3.group('p2')
                if df.loc[row,'HomeTeam'] == df.loc[row,'EventTeam']:   
                    dtrow['EventTeam'] = df.loc[row,'AwayTeam']
                else:
                    dtrow['EventTeam'] = df.loc[row,'HomeTeam']
                temp_df_dts.append(list(dtrow))
        
        #Double Fouls
        if event == 'Foul : Double Personal':
            df.loc[row,'Event'] = 'Foul'
            df.loc[row,'FoulType'] = 'Double Personal'
            match3 = re.match(r"Foul : Double Personal - (?P<player1>[\w\s\-']*) \((?P<stat1>[0-9]) PF\), (?P<player2>[\w\s\-']*) \((?P<stat2>[0-9]) PF\)",string)
            df.loc[row,'Foul'] = match3.group('player1')
            df.loc[row,'EventPlayer'] = match3.group('player1')
            df.loc[row,'EventTeam'] = team_ids[df.loc[row,'tid']]
            df.loc[row,'FoulNumFouls'] = match3.group('stat1')
            #dfrow = df.iloc[row]
            #dfrow['Foul'] = match3.group('player2')
            #dfrow['FoulNumFouls'] = match3.group('stat2')
            #temp_df_dfs.append(list(dfrow))


<ipython-input-122-ae8232ec2ebb>:173: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dtrow['EventPlayer'] = match3.group('p2')
<ipython-input-122-ae8232ec2ebb>:175: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dtrow['EventTeam'] = df.loc[row,'AwayTeam']


In [123]:
#temp_df_dfs = pd.DataFrame(temp_df_dfs, columns=df.columns)
#df = df.append(temp_df_dfs, ignore_index=False)
#
temp_df_dts = pd.DataFrame(temp_df_dts, columns=df.columns)
df = df.append(temp_df_dts, ignore_index=False)

#df = df.sort_values('index').reset_index()
#del df['index']
#del df['level_0']

In [124]:
df = df.sort_values('Time',ascending=False)
df = df.sort_values(['GameID','Quarter'])
df = df.reset_index()
del df['index']

In [125]:
g = df.groupby(['pid','EventPlayer'])
d = g.last()
d = d.reset_index()
players = {}
for row in range(len(d)):
    players[d.loc[row,'pid']] = d.loc[row,'EventPlayer']
    if d.loc[row,'EventPlayer'] == 'Team':
        players[d.loc[row,'pid']] = d.loc[row,'EventTeam']

In [126]:
#df.to_csv('test.csv')
df.to_csv('data/wnba-pbp-'+year+'.csv')